## SQLite and Python

In the lecture we have talked about Databases and particulartly relational databases such as [SQLite](https://www.sqlite.org/). Relational databases use tables (relations) as a central structure for data storage. The standard language to interact with relational databases is SQL, which serves both as a 
* *Data Definition Language (DDL)* - to create, alter, and drop tables, constraints on the data and other objects such as views, indexes, etc. as well as
* *Data Manipultation Language (DML)* - to insert and update data in tables, as well as to query data.
 
You could work with SQLite from a command line or using a tool such as [DB Browser for SQLite](http://sqlitebrowser.org/). In the following, we will have a look at using SQLite together with Python with the help of the [sqlite3 package](https://docs.python.org/3/library/sqlite3.html):

In [ ]:
import sqlite3

First you have to define a `connection` to the database: the function `connect()` creates a new database session and returns a new `connection` instance.  The class `connection` encapsulates a database session. It allows you to e.g. create new `cursor` using the `cursor()` method to execute database commands and queries.

You can use a cursor to execute DDL+DML statements: the class `cursor` allows interaction with the database:
* send commands to the database using methods such as `execute()` and `executemany()`,
* retrieve data from the database by iteration or using methods such as `fetchone()`, `fetchmany()`, `fetchall()`.

Note that in the end, you have to:
 * commit changes to be written into in your database persistently (if you have done updates, insertions, or deletions)
 * close both the cursor and the connection

### Create Table

In [ ]:
#Open the connection:
with sqlite3.connect('../mydb') as conn:
    cur = conn.cursor()
    
    #-- drop the table if it already exists:
    cur.execute("DROP TABLE test_persons;")
    cur.execute("DROP TABLE test_data;")
    
    #create a new table
    cur.execute("CREATE TABLE test_persons (personID INTEGER PRIMARY KEY, name TEXT NOT NULL, address TEXT);")
    #fill the table with data
    cur.execute("INSERT INTO test_persons VALUES (1, 'Jennifer Brown', 'Some Street 1, Some City');")
    cur.execute("INSERT INTO test_persons VALUES (2, 'Peter Stone', 'Some Street 2, Some City');")
    cur.execute("INSERT INTO test_persons VALUES (3, 'Gerry Small', 'Some Street 123, Some City');")
    cur.execute("INSERT INTO test_persons VALUES (4, 'Peter Watson', 'Some Square 5, Some City');")
    cur.execute("INSERT INTO test_persons VALUES (5, 'Jason Stark', 'Some House 1, Some City');")
    
    #create a new table
    cur.execute("CREATE TABLE test_data (entryID INTEGER PRIMARY KEY, test_person INTEGER, points INTEGER, date TEXT);")
    #this time, we can insert the data in bulk (as an example)
    test_data_values = [(123, 1, 75, "2017-06-05"), (124, 1, 85, "2016-01-13"), (125, 2, 77, "2017-06-05"), (126, 4, 99, "2017-06-05"), (127, 5, 100, "2016-01-13")]
    cur.executemany("INSERT INTO test_data VALUES (?,?,?,?)",test_data_values)
    
    #updating works too
    cur.execute("UPDATE test_data SET points = 88  WHERE entryID = 124")
    
    #make the chages permanent
    conn.commit()
    cur.close()

### Quering data

In [ ]:
#Open the connection:
with sqlite3.connect('../mydb') as conn:
    cur = conn.cursor()
    
    # Query the database and obtain data as Python (tuple) objects
    cur.execute("SELECT * FROM test_persons;")
    print(cur.fetchall())
    
    # Close communication (both the cursor and the connection) with the database
    cur.close()

### Loading data from a CSV file into a table

In [ ]:
import csv, sqlite3

#database can be loaded into working memory
conn = sqlite3.connect(":memory:")
sqlite3.connect('../allcourses')

cur = conn.cursor()

#cur.execute("DROP TABLE allcourses;")
cur.execute("CREATE TABLE allcourses (course_id, semester, name, roomcode, buildingname, start, end);")

with open('data/allcoursesandevents16w-small.csv','r') as csvfile: 
    # csv.DictReader uses first line in file for column headings by default
    data = csv.DictReader(csvfile) # you could define a delimiter, but the data uses the dafault comma
    insert_this = [(i['course_id'], i['semester'], i['name'], i['roomcode'], i['buildingname'], i['start'], i['end']) for i in data]

cur.executemany("INSERT INTO allcourses (course_id, semester, name, roomcode, buildingname, start, end) VALUES (?, ?, ?, ?, ?, ?, ?);", insert_this)
conn.commit()

cur.execute("SELECT * FROM allcourses LIMIT 1;")
print([i[0] for i in cur.description])
print(cur.fetchall())
conn.close()

## A more complex use case around our City Data use case

Now that we know how to establish some basic interaction with a database, let's try to solve the following task.
We learnt how to do filtering and merging of data with Python in Units 3 and 4.

This can be actually done within a database as well:
* Store the the EUROSTAT populations table, the iso country codes table, 
  and the indicator tables in the database in the database.
* Formulate an SQL query that gets me the 2014 average populations for cities per country, ordered by the country name.

**Discuss**: What's better? Doing it directly in Python, or doing it in SQL? Discuss pros and cons!


In [ ]:
import csv

cityCodeFile="./data/cities.csv"
conn = sqlite3.connect('../citydata')
cur = conn.cursor()

# We create a table from the first 7 columns of the file: 
with open(cityCodeFile) as f:
    csvfile = csv.reader(f)
    
    #the column names are extracted from the CSV header row
    header = "CREATE TABLE cityCodeFile_raw ("+ ', '.join([col.replace('"', '') + " TEXT " for col in (next(csvfile))[:7]]) + ");"

    cur.execute(header)

    for row in csvfile:
        cur.execute("INSERT INTO cityCodeFile_raw VALUES ("+ ','.join(["'" + str(i).replace("'", '"') + "'" for i in row[:7]]) + ")")
        
conn.commit()
cur.close()
conn.close()

Can you test what the data inside looks like?

## Connecting to a Different Existing Database Server

Connecting to an existing SQL Database __server__ works much similar to working with SQL Lite. There are different libraries and connectors available for Python. In this example, we will use [psycopg](http://initd.org/psycopg/), which is a library to connect to [PostgreSQL](https://www.postgresql.org/) databases:

In [ ]:
import psycopg2

_(NOTE: You might see a warning upon import, which you can sefely ignore)_

In order to connect to a Database server, we need 

* its _host address_ (e.g. `balrog.wu.ac.at` which some of you already know, as the database server we used in the Database Systems lecture)
* a _database_ to connect to, 
* as well as a _username_ and _password_

Let's use a simple helper function in order not to have to type in the password in plaintext:

In [ ]:
# Getpass prompts for a password: This is just to not have to type in my password verabtim into the notebook:
import getpass
password = getpass.getpass()

Now we are ready to create the full connection parameters string:

In [ ]:
connectionparams = "dbname=apollere user=apollere host=balrog.wu.ac.at password="+password

From here onwards, the psycopg2 connector works just the same as the sqlite3 package: 

In [ ]:
# The psycopg package works very similar to the sqlite one:
with psycopg2.connect(connectionparams) as conn:
    cur = conn.cursor()
    cur.execute("SELECT * FROM books")
    print(cur.fetchall())
    cur.close()